# Thu thập Dữ liệu thời tiết từ API Visual Crossing

Tên: Lê Thành Đạt

MSSV: 22120053

Nhóm: 5 - Turtles

## 1. Giới thiệu

Trong giai đoạn thu thập dữ liệu (data collection) theo quy trình của đồ án, em sử dụng [API Visual Crossing](https://www.visualcrossing.com/) để nhằm thu thập dữ liệu thời tiết tại hai khu vực của Việt Nam: Hà Nội (vùng đồng bằng sông Hồng) và Nghệ An (khu vực Bắc Trung Bộ). Việc thu thập dữ liệu trong những vùng có đặc điểm khí hậu khác nhau này sẽ hỗ trợ phân tích các xu hướng thời tiết đặc trưng của từng khu vực, đặc biệt là khi chúng chịu ảnh hưởng của các hệ thống thời tiết khác nhau. Việc sử dụng API Visual Crossing sẽ cho phép truy cập dữ liệu thời tiết theo lịch sử với nhiều chỉ số hữu ích.

## 2. Thiết lập API và Chiến lược Thu thập Dữ liệu

Visual Crossing API cho phép truy vấn theo ngày với giới hạn truy vấn tùy thuộc vào gói sử dụng, ở đây tối đa 1000 bản ghi mỗi ngày. Do giới hạn về số lượng bản ghi trong mỗi lần truy vấn, em chia quá trình thu thập thành 4 đợt, mỗi ngày thu thập gần 1000 bản ghi:
- Đợt thứ nhất: Từ ngày 1/1/2019 đến 31/8/2021 ở Hà Nội.
- Đợt thứ hai: Từ ngày 1/9/2021 đến 1/1/2024 ở Hà Nội.
- Đợt thứ ba: Từ ngày 1/1/2019 đến 31/8/2021 ở Nghệ An.
- Đợt thứ tư: Từ ngày 1/9/2021 đến 1/1/2024 ở Nghệ An.

## 3. Thiết Lập Môi Trường

In [1]:
# import các thư viện cần thiết
import requests
from pprint import pprint
import pandas as pd

API_KEY = 'DDNS9H49F7WPBGMEAKXV49NEU'
BASE_URL = 'https://weather.visualcrossing.com/VisualCrossingWebServices/rest/services/timeline'
locations = ["Hanoi", "Nghe An"]

[Weather Data Documentation](https://www.visualcrossing.com/resources/documentation/weather-data/weather-data-documentation/)

In [2]:
# Danh sách các đặc trưng cần trích xuất của từng ngày từ dữ liệu thời tiết
ATTRIBUTE = [
    'datetime',       # ngày
    'tempmax',        # nhiệt độ cao nhất
    'tempmin',        # nhiệt độ thấp nhất
    'temp',           # nhiệt độ (nhiệt độ trung bình)
    'dew',            # điểm sương (độ ẩm ngưng tụ) (độ C) 
    'feelslike',      # cảm giác như
    'precip',         # precipitation - lượng mưa
    'precipprob',     # xác suất mưa (%)
    'precipcover',    # độ che phủ mưa
    'preciptype',     # loại mưa
    'snow',           # lượng tuyết rơi
    'snowdepth',      # độ sâu tuyết
    'windspeed',      # tốc độ gió (km/h)
    'windgust',       # gió giật
    'winddir',        # hướng gió 
    'visibility',     # tầm nhìn xa
    'cloudcover',     # % mây che phủ
    'humidity',       # độ ẩm tương đối
    'pressure',       # sea level pressure - áp suất ở mực nước biển
    'solarradiation', # bức xạ mặt trời
    'solarenergy',    # năng lượng mặt trời
    'uvindex',        # chỉ số UV
    #'severerisk',    # rủi ro nghiêm trọng (không thể trích xuất)
    'sunrise',        # thời gian mặt trời mọc
    'sunset',         # thời gian hoàng hôn
    'moonphase',      # pha mặt trăng
    'icon',           # biểu tượng thời tiết
    'conditions',     # mô tả ngắn về điều kiện thời tiết
    'description',    # mô tả chi tiết
    'stations'        # mã các trạm thời tiết
]

### Thu thập và Chuyển đổi Dữ liệu Thời tiết từ Visual Crossing API

In [3]:
def fetch_weather_data(location, date1, date2):
    URL = f"{BASE_URL}/{location}/{date1}/{date2}"
    params = {
        "key": API_KEY, # API của tài khoản do Visual Crossing cung cấp
        "unitGroup": "metric",  # Nhóm đơn vị đo là độ C
        "include": "days",   # Lấy dữ liệu thời tiết hiện tại
        "contentType": "json",  # Định dạng trả về là JSON
        "lang" : "en"
    }
    
    response = requests.get(URL, params=params)
    
    if response.status_code == 200:
        return response.json()
    else:
        print(f"Error fetching data")
        return None

# Kiểm tra dữ liệu
def print_data(data):
    print(data['days'][0]['datetime'], data['days'][len(data['days']) - 1]['datetime'])
    print(data.keys())
    print(type(data['days']))
    # In ra dữ liệu của ngày đầu tiên trong dữ liệu
    pprint(data['days'][0])
    
def convert_to_table(data):
    table = {}
    
    # Thêm các cột với tên đã viết hoa chữ cái đầu
    for col in ATTRIBUTE + ['address']:
        table[col.capitalize()] = []

    # Lặp qua từng ngày và thêm dữ liệu vào bảng
    for day in data['days']:
        for col in ATTRIBUTE:
            table[col.capitalize()].append(day[col])
        table['Address'].append(data['address'])
        
    return table

#### Đợt thứ nhất: Từ ngày 1/1/2019 đến 31/8/2021 ở Hà Nội.

In [4]:
data = fetch_weather_data(locations[0], '2019-01-01', '2021-08-31')
print_data(data)

2019-01-01 2021-08-31
dict_keys(['queryCost', 'latitude', 'longitude', 'resolvedAddress', 'address', 'timezone', 'tzoffset', 'days', 'stations'])
<class 'list'>
{'cloudcover': 88.3,
 'conditions': 'Partially cloudy',
 'datetime': '2019-01-01',
 'datetimeEpoch': 1546275600,
 'description': 'Partly cloudy throughout the day.',
 'dew': 5.3,
 'feelslike': 11.8,
 'feelslikemax': 13.0,
 'feelslikemin': 11.0,
 'humidity': 64.5,
 'icon': 'partly-cloudy-day',
 'moonphase': 0.83,
 'precip': 0.0,
 'precipcover': 0.0,
 'precipprob': 0.0,
 'preciptype': None,
 'pressure': 1028.4,
 'snow': 0.0,
 'snowdepth': 0.0,
 'solarenergy': 4.3,
 'solarradiation': 50.8,
 'source': 'obs',
 'stations': ['48820099999',
              '48823099999',
              '48825099999',
              '48831099999',
              'VVNB'],
 'sunrise': '06:33:36',
 'sunriseEpoch': 1546299216,
 'sunset': '17:26:14',
 'sunsetEpoch': 1546338374,
 'temp': 11.8,
 'tempmax': 13.0,
 'tempmin': 11.0,
 'uvindex': 2.0,
 'visibility': 10.

In [5]:
# In ra dữ liệu theo định dạng JSON đã thu thập được từ API
pprint(data)

{'address': 'Hanoi',
 'days': [{'cloudcover': 88.3,
           'conditions': 'Partially cloudy',
           'datetime': '2019-01-01',
           'datetimeEpoch': 1546275600,
           'description': 'Partly cloudy throughout the day.',
           'dew': 5.3,
           'feelslike': 11.8,
           'feelslikemax': 13.0,
           'feelslikemin': 11.0,
           'humidity': 64.5,
           'icon': 'partly-cloudy-day',
           'moonphase': 0.83,
           'precip': 0.0,
           'precipcover': 0.0,
           'precipprob': 0.0,
           'preciptype': None,
           'pressure': 1028.4,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 4.3,
           'solarradiation': 50.8,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
                        'VVNB'],
           'sunrise': '06:33:36',
           'sunriseEpoch':

           'dew': 20.2,
           'feelslike': 23.1,
           'feelslikemax': 26.5,
           'feelslikemin': 21.0,
           'humidity': 84.8,
           'icon': 'rain',
           'moonphase': 0.98,
           'precip': 0.098,
           'precipcover': 4.17,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1016.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 9.4,
           'solarradiation': 107.2,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
                        'VVNB'],
           'sunrise': '06:32:40',
           'sunriseEpoch': 1549236760,
           'sunset': '17:48:28',
           'sunsetEpoch': 1549277308,
           'temp': 23.1,
           'tempmax': 26.5,
           'tempmin': 21.0,
           'uvindex': 5.0,
           'visibility': 7.6,
           'windd

           'temp': 30.0,
           'tempmax': 33.7,
           'tempmin': 27.0,
           'uvindex': 8.0,
           'visibility': 8.8,
           'winddir': 107.4,
           'windgust': 21.6,
           'windspeed': 14.8},
          {'cloudcover': 55.0,
           'conditions': 'Partially cloudy',
           'datetime': '2019-07-27',
           'datetimeEpoch': 1564160400,
           'description': 'Partly cloudy throughout the day.',
           'dew': 26.0,
           'feelslike': 38.8,
           'feelslikemax': 43.4,
           'feelslikemin': 35.6,
           'humidity': 76.0,
           'icon': 'partly-cloudy-day',
           'moonphase': 0.84,
           'precip': 0.0,
           'precipcover': 0.0,
           'precipprob': 0.0,
           'preciptype': None,
           'pressure': 1003.5,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 22.6,
           'solarradiation': 260.7,
           'source': 'obs',
           'stations': ['48820099999',
 

           'moonphase': 0.05,
           'precip': 0.293,
           'precipcover': 4.17,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1006.1,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 14.2,
           'solarradiation': 165.8,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
                        'VVNB'],
           'sunrise': '05:16:00',
           'sunriseEpoch': 1590272160,
           'sunset': '18:31:06',
           'sunsetEpoch': 1590319866,
           'temp': 29.2,
           'tempmax': 33.3,
           'tempmin': 25.0,
           'uvindex': 5.0,
           'visibility': 9.1,
           'winddir': 94.6,
           'windgust': 25.6,
           'windspeed': 19.4},
          {'cloudcover': 49.3,
           'conditions': 'Rain, Partially cloudy',
           'datetime':

           'visibility': 9.3,
           'winddir': 95.5,
           'windgust': 23.8,
           'windspeed': 16.6},
          {'cloudcover': 56.8,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2020-10-02',
           'datetimeEpoch': 1601571600,
           'description': 'Partly cloudy throughout the day with rain.',
           'dew': 24.4,
           'feelslike': 31.8,
           'feelslikemax': 37.9,
           'feelslikemin': 26.0,
           'humidity': 79.8,
           'icon': 'rain',
           'moonphase': 0.5,
           'precip': 0.216,
           'precipcover': 12.5,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1008.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 12.7,
           'solarradiation': 146.5,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                     

           'tempmin': 17.0,
           'uvindex': 3.0,
           'visibility': 2.5,
           'winddir': 65.8,
           'windgust': 20.2,
           'windspeed': 11.2},
          {'cloudcover': 77.9,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2021-03-06',
           'datetimeEpoch': 1614963600,
           'description': 'Partly cloudy throughout the day with rain.',
           'dew': 20.2,
           'feelslike': 23.2,
           'feelslikemax': 28.7,
           'feelslikemin': 19.9,
           'humidity': 85.8,
           'icon': 'rain',
           'moonphase': 0.75,
           'precip': 0.395,
           'precipcover': 8.33,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1013.7,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 12.3,
           'solarradiation': 143.0,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
    

           'pressure': 1006.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 17.8,
           'solarradiation': 206.9,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
                        'VVNB'],
           'sunrise': '05:34:19',
           'sunriseEpoch': 1628721259,
           'sunset': '18:28:44',
           'sunsetEpoch': 1628767724,
           'temp': 27.3,
           'tempmax': 32.4,
           'tempmin': 24.0,
           'uvindex': 8.0,
           'visibility': 8.4,
           'winddir': 75.4,
           'windgust': 29.5,
           'windspeed': 16.6},
          {'cloudcover': 79.8,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2021-08-13',
           'datetimeEpoch': 1628787600,
           'description': 'Partly cloudy throughout the day with early morning '
                     

In [6]:
table = convert_to_table(data)
df = pd.DataFrame(table)

In [7]:
df.to_csv('HaNoi.csv', sep=',', encoding='utf-8', index=False, header=True)

#### Đợt thứ hai: Từ ngày 1/9/2021 đến 1/1/2024 ở Hà Nội.

In [8]:
data = fetch_weather_data(locations[0], '2021-09-01', '2024-01-01')
print_data(data)

2021-09-01 2024-01-01
dict_keys(['queryCost', 'latitude', 'longitude', 'resolvedAddress', 'address', 'timezone', 'tzoffset', 'days', 'stations'])
<class 'list'>
{'cloudcover': 33.8,
 'conditions': 'Rain, Partially cloudy',
 'datetime': '2021-09-01',
 'datetimeEpoch': 1630429200,
 'description': 'Partly cloudy throughout the day with afternoon rain.',
 'dew': 25.1,
 'feelslike': 35.4,
 'feelslikemax': 40.7,
 'feelslikemin': 26.5,
 'humidity': 77.6,
 'icon': 'rain',
 'moonphase': 0.81,
 'precip': 18.543,
 'precipcover': 4.17,
 'precipprob': 100.0,
 'preciptype': ['rain'],
 'pressure': 1008.5,
 'snow': 0.0,
 'snowdepth': 0.0,
 'solarenergy': 20.1,
 'solarradiation': 232.9,
 'source': 'obs',
 'stations': ['48820099999',
              '48823099999',
              '48825099999',
              '48831099999',
              'VVNB'],
 'sunrise': '05:40:10',
 'sunriseEpoch': 1630449610,
 'sunset': '18:12:48',
 'sunsetEpoch': 1630494768,
 'temp': 29.9,
 'tempmax': 34.0,
 'tempmin': 26.5,
 'uvindex

In [9]:
# In ra dữ liệu theo định dạng JSON đã thu thập được từ API
pprint(data)

{'address': 'Hanoi',
 'days': [{'cloudcover': 33.8,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2021-09-01',
           'datetimeEpoch': 1630429200,
           'description': 'Partly cloudy throughout the day with afternoon '
                          'rain.',
           'dew': 25.1,
           'feelslike': 35.4,
           'feelslikemax': 40.7,
           'feelslikemin': 26.5,
           'humidity': 77.6,
           'icon': 'rain',
           'moonphase': 0.81,
           'precip': 18.543,
           'precipcover': 4.17,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1008.5,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 20.1,
           'solarradiation': 232.9,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
                        'VVNB'],
     

           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
                        'VVNB'],
           'sunrise': '05:42:24',
           'sunriseEpoch': 1631227344,
           'sunset': '18:04:33',
           'sunsetEpoch': 1631271873,
           'temp': 29.2,
           'tempmax': 34.4,
           'tempmin': 25.0,
           'uvindex': 9.0,
           'visibility': 9.2,
           'winddir': 292.0,
           'windgust': 25.2,
           'windspeed': 14.8},
          {'cloudcover': 59.5,
           'conditions': 'Partially cloudy',
           'datetime': '2021-09-11',
           'datetimeEpoch': 1631293200,
           'description': 'Partly cloudy throughout the day.',
           'dew': 24.2,
           'feelslike': 34.6,
           'feelslikemax': 42.1,
           'feelslikemin': 25.0,
           'humidity': 72.9,
           'icon': 'partly-cloudy-day',
           'moonphase': 0.15,
     

          {'cloudcover': 99.1,
           'conditions': 'Overcast',
           'datetime': '2022-02-03',
           'datetimeEpoch': 1643821200,
           'description': 'Cloudy skies throughout the day.',
           'dew': 7.3,
           'feelslike': 14.0,
           'feelslikemax': 16.5,
           'feelslikemin': 12.0,
           'humidity': 64.9,
           'icon': 'cloudy',
           'moonphase': 0.06,
           'precip': 0.0,
           'precipcover': 0.0,
           'precipprob': 0.0,
           'preciptype': None,
           'pressure': 1020.6,
           'severerisk': 10.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 10.3,
           'solarradiation': 118.3,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
                        'VVNB'],
           'sunrise': '06:32:58',
           'sunriseEpoch': 1643844

           'feelslikemin': 23.0,
           'humidity': 74.8,
           'icon': 'partly-cloudy-day',
           'moonphase': 0.17,
           'precip': 0.0,
           'precipcover': 0.0,
           'precipprob': 0.0,
           'preciptype': None,
           'pressure': 1010.9,
           'severerisk': 10.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 26.3,
           'solarradiation': 302.6,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
                        'VVNB'],
           'sunrise': '05:23:26',
           'sunriseEpoch': 1651789406,
           'sunset': '18:23:21',
           'sunsetEpoch': 1651836201,
           'temp': 26.0,
           'tempmax': 29.6,
           'tempmin': 23.0,
           'uvindex': 10.0,
           'visibility': 8.5,
           'winddir': 50.2,
           'windgust': 29.5,
          

          {'cloudcover': 59.5,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2022-06-13',
           'datetimeEpoch': 1655053200,
           'description': 'Partly cloudy throughout the day with late '
                          'afternoon rain.',
           'dew': 25.7,
           'feelslike': 37.7,
           'feelslikemax': 45.3,
           'feelslikemin': 25.8,
           'humidity': 75.4,
           'icon': 'rain',
           'moonphase': 0.46,
           'precip': 0.168,
           'precipcover': 4.17,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1003.1,
           'severerisk': 60.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 24.1,
           'solarradiation': 278.2,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
                        

...

           'solarradiation': 215.5,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
                        'VVNB'],
           'sunrise': '06:36:14',
           'sunriseEpoch': 1673652974,
           'sunset': '17:34:50',
           'sunsetEpoch': 1673692490,
           'temp': 24.3,
           'tempmax': 32.0,
           'tempmin': 19.8,
           'uvindex': 8.0,
           'visibility': 9.1,
           'winddir': 54.6,
           'windgust': 23.0,
           'windspeed': 14.8},
          {'cloudcover': 81.2,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2023-01-15',
           'datetimeEpoch': 1673715600,
           'description': 'Partly cloudy throughout the day with late '
                          'afternoon rain.',
           'dew': 14.7,
           'feelslike': 19.7,
           'feelslikemax': 22.4,
           'fe

          {'cloudcover': 73.4,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2023-04-24',
           'datetimeEpoch': 1682269200,
           'description': 'Partly cloudy throughout the day with rain in the '
                          'morning and afternoon.',
           'dew': 24.8,
           'feelslike': 32.0,
           'feelslikemax': 40.7,
           'feelslikemin': 26.0,
           'humidity': 82.2,
           'icon': 'rain',
           'moonphase': 0.13,
           'precip': 0.5,
           'precipcover': 12.5,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1010.2,
           'severerisk': 60.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 11.2,
           'solarradiation': 130.5,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
            

          {'cloudcover': 90.9,
           'conditions': 'Rain, Overcast',
           'datetime': '2023-07-19',
           'datetimeEpoch': 1689699600,
           'description': 'Cloudy skies throughout the day with a chance of '
                          'rain throughout the day.',
           'dew': 24.4,
           'feelslike': 28.4,
           'feelslikemax': 34.5,
           'feelslikemin': 24.7,
           'humidity': 89.0,
           'icon': 'rain',
           'moonphase': 0.05,
           'precip': 14.587,
           'precipcover': 16.67,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1003.6,
           'severerisk': 30.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 11.1,
           'solarradiation': 128.2,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
               

          {'cloudcover': 87.9,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2023-11-06',
           'datetimeEpoch': 1699203600,
           'description': 'Partly cloudy throughout the day with rain.',
           'dew': 23.2,
           'feelslike': 26.8,
           'feelslikemax': 36.0,
           'feelslikemin': 22.0,
           'humidity': 86.1,
           'icon': 'rain',
           'moonphase': 0.77,
           'precip': 7.515,
           'precipcover': 8.33,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1014.9,
           'severerisk': 30.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 13.8,
           'solarradiation': 159.6,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
                        'VVNB'],
           'sunrise': '06:01:28',
 

           'windspeed': 10.3},
          {'cloudcover': 65.0,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2023-12-31',
           'datetimeEpoch': 1703955600,
           'description': 'Partly cloudy throughout the day with rain.',
           'dew': 18.6,
           'feelslike': 22.3,
           'feelslikemax': 25.5,
           'feelslikemin': 20.0,
           'humidity': 80.4,
           'icon': 'rain',
           'moonphase': 0.64,
           'precip': 0.1,
           'precipcover': 8.33,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1017.3,
           'severerisk': 10.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 11.7,
           'solarradiation': 135.6,
           'source': 'obs',
           'stations': ['48820099999',
                        '48823099999',
                        '48825099999',
                        '48831099999',
                        'VVNB'],
      

In [11]:
table = convert_to_table(data)
df_new = pd.DataFrame(table)

In [12]:
df_old = pd.read_csv('HaNoi.csv')
df_old.head(5)

Datetime  Tempmax  Tempmin  Temp   Dew  Feelslike  Precip  Precipprob  \
0  2019-01-01     13.0     11.0  11.8   5.3       11.8   0.000         0.0   
1  2019-01-02     17.0     11.5  14.1   7.0       14.1   0.100       100.0   
2  2019-01-03     18.1     13.0  15.3   9.0       15.3   0.010       100.0   
3  2019-01-04     19.0     13.0  16.3  12.4       16.3   0.878       100.0   
4  2019-01-05     22.0     16.0  19.0  15.1       19.0   0.000         0.0   

   Precipcover Preciptype  ...  Solarenergy  Uvindex   Sunrise    Sunset  \
0         0.00        NaN  ...          4.3      2.0  06:33:36  17:26:14   
1         4.17   ['rain']  ...          3.8      2.0  06:33:55  17:26:51   
2         4.17   ['rain']  ...          3.8      2.0  06:34:13  17:27:29   
3         4.17   ['rain']  ...          3.9      2.0  06:34:30  17:28:08   
4         0.00        NaN  ...          7.8      4.0  06:34:46  17:28:47   

   Moonphase               Icon              Conditions  \
0       0.83  partly-cloudy-day        Partially cloudy   
1       0.87               rain  Rain, Partially cloudy   
2       0.90               rain  Rain, Partially cloudy   
3       0.94               rain  Rain, Partially cloudy   
4       0.97  partly-cloudy-day        Partially cloudy   

                                         Description  \
0                  Partly cloudy throughout the day.   
1  Partly cloudy throughout the day with late aft...   
2  Partly cloudy throughout the day with afternoo...   
3  Partly cloudy throughout the day with morning ...   
4                  Partly cloudy throughout the day.   

                                            Stations  Address  
0  ['48820099999', '48823099999', '48825099999', ...    Hanoi  
1  ['48820099999', '48823099999', '48825099999', ...    Hanoi  
2  ['48820099999', '48823099999', '48825099999', ...    Hanoi  
3  ['48820099999', '48823099999', '48825099999', ...    Hanoi  
4  ['48820099999', '48823099999', '48825099999', ...    Hanoi  

[5 rows x 30 columns]

In [13]:
df_combined = pd.concat([df_old, df_new], ignore_index=True)
df_combined.to_csv('HaNoi.csv', sep=',', encoding='utf-8', index=False, header=True)

#### Đợt thứ ba: Từ ngày 1/1/2019 đến 31/8/2021 ở Nghệ An.

In [4]:
data = fetch_weather_data(locations[1], '2019-01-01', '2021-08-31')
print_data(data)

2019-01-01 2021-08-31
dict_keys(['queryCost', 'latitude', 'longitude', 'resolvedAddress', 'address', 'timezone', 'tzoffset', 'days', 'stations'])
<class 'list'>
{'cloudcover': 100.0,
 'conditions': 'Overcast',
 'datetime': '2019-01-01',
 'datetimeEpoch': 1546275600,
 'description': 'Cloudy skies throughout the day.',
 'dew': 10.3,
 'feelslike': 14.0,
 'feelslikemax': 15.0,
 'feelslikemin': 12.9,
 'humidity': 78.7,
 'icon': 'cloudy',
 'moonphase': 0.83,
 'precip': 0.0,
 'precipcover': 0.0,
 'precipprob': 0.0,
 'preciptype': None,
 'pressure': 1026.4,
 'snow': 0.0,
 'snowdepth': 0.0,
 'solarenergy': 4.6,
 'solarradiation': 52.1,
 'source': 'obs',
 'stations': ['48845099999', 'remote', '48846099999'],
 'sunrise': '06:29:44',
 'sunriseEpoch': 1546298984,
 'sunset': '17:31:24',
 'sunsetEpoch': 1546338684,
 'temp': 14.0,
 'tempmax': 15.0,
 'tempmin': 12.9,
 'uvindex': 2.0,
 'visibility': 19.9,
 'winddir': 335.4,
 'windgust': 36.0,
 'windspeed': 20.9}


In [5]:
# In ra dữ liệu theo định dạng JSON đã thu thập được từ API
pprint(data)

{'address': 'Nghe An',
 'days': [{'cloudcover': 100.0,
           'conditions': 'Overcast',
           'datetime': '2019-01-01',
           'datetimeEpoch': 1546275600,
           'description': 'Cloudy skies throughout the day.',
           'dew': 10.3,
           'feelslike': 14.0,
           'feelslikemax': 15.0,
           'feelslikemin': 12.9,
           'humidity': 78.7,
           'icon': 'cloudy',
           'moonphase': 0.83,
           'precip': 0.0,
           'precipcover': 0.0,
           'precipprob': 0.0,
           'preciptype': None,
           'pressure': 1026.4,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 4.6,
           'solarradiation': 52.1,
           'source': 'obs',
           'stations': ['48845099999', 'remote', '48846099999'],
           'sunrise': '06:29:44',
           'sunriseEpoch': 1546298984,
           'sunset': '17:31:24',
           'sunsetEpoch': 1546338684,
           'temp': 14.0,
           'tempmax': 15.0,
   

          {'cloudcover': 86.4,
           'conditions': 'Partially cloudy',
           'datetime': '2019-08-13',
           'datetimeEpoch': 1565629200,
           'description': 'Partly cloudy throughout the day.',
           'dew': 23.6,
           'feelslike': 37.3,
           'feelslikemax': 41.7,
           'feelslikemin': 34.5,
           'humidity': 61.8,
           'icon': 'partly-cloudy-day',
           'moonphase': 0.42,
           'precip': 0.0,
           'precipcover': 0.0,
           'precipprob': 0.0,
           'preciptype': None,
           'pressure': 1002.3,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 19.8,
           'solarradiation': 229.9,
           'source': 'obs',
           'stations': ['48845099999', 'remote', '48846099999'],
           'sunrise': '05:38:01',
           'sunriseEpoch': 1565649481,
           'sunset': '18:26:10',
           'sunsetEpoch': 1565695570,
           'temp': 31.9,
           'tempmax': 34.8,
     

           'feelslikemax': 32.5,
           'feelslikemin': 23.4,
           'humidity': 89.0,
           'icon': 'rain',
           'moonphase': 0.03,
           'precip': 0.5,
           'precipcover': 16.67,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1009.7,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 16.5,
           'solarradiation': 191.1,
           'source': 'obs',
           'stations': ['48845099999', 'remote', '48846099999'],
           'sunrise': '05:57:03',
           'sunriseEpoch': 1585090623,
           'sunset': '18:09:29',
           'sunsetEpoch': 1585134569,
           'temp': 25.3,
           'tempmax': 28.4,
           'tempmin': 23.4,
           'uvindex': 7.0,
           'visibility': 20.0,
           'winddir': 137.7,
           'windgust': 27.4,
           'windspeed': 16.2},
          {'cloudcover': 33.1,
           'conditions': 'Partially cloudy',
           'datetime': '2020-

           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1006.2,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 21.8,
           'solarradiation': 250.6,
           'source': 'obs',
           'stations': ['48845099999', 'remote'],
           'sunrise': '05:42:17',
           'sunriseEpoch': 1598827337,
           'sunset': '18:12:30',
           'sunsetEpoch': 1598872350,
           'temp': 30.9,
           'tempmax': 33.7,
           'tempmin': 27.7,
           'uvindex': 8.0,
           'visibility': 20.0,
           'winddir': 19.6,
           'windgust': 22.0,
           'windspeed': 10.8},
          {'cloudcover': 54.0,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2020-09-01',
           'datetimeEpoch': 1598893200,
           'description': 'Partly cloudy throughout the day with afternoon '
                          'rain.',
           'dew': 26.0,
           'feelslike': 37.9,
       

           'feelslike': 18.0,
           'feelslikemax': 20.1,
           'feelslikemin': 16.3,
           'humidity': 75.9,
           'icon': 'cloudy',
           'moonphase': 0.28,
           'precip': 0.0,
           'precipcover': 0.0,
           'precipprob': 0.0,
           'preciptype': None,
           'pressure': 1017.1,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 5.9,
           'solarradiation': 68.7,
           'source': 'obs',
           'stations': ['48845099999', 'remote'],
           'sunrise': '06:26:13',
           'sunriseEpoch': 1608679573,
           'sunset': '17:26:37',
           'sunsetEpoch': 1608719197,
           'temp': 18.0,
           'tempmax': 20.1,
           'tempmin': 16.3,
           'uvindex': 3.0,
           'visibility': 20.0,
           'winddir': 328.9,
           'windgust': 24.1,
           'windspeed': 11.9},
          {'cloudcover': 95.8,
           'conditions': 'Rain, Overcast',
           'datetime': '

          {'cloudcover': 42.8,
           'conditions': 'Partially cloudy',
           'datetime': '2021-05-14',
           'datetimeEpoch': 1620925200,
           'description': 'Partly cloudy throughout the day.',
           'dew': 26.5,
           'feelslike': 37.1,
           'feelslikemax': 43.5,
           'feelslikemin': 26.7,
           'humidity': 83.6,
           'icon': 'partly-cloudy-day',
           'moonphase': 0.08,
           'precip': 0.0,
           'precipcover': 0.0,
           'precipprob': 0.0,
           'preciptype': None,
           'pressure': 1004.9,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 24.8,
           'solarradiation': 287.1,
           'source': 'obs',
           'stations': ['48845099999', 'remote'],
           'sunrise': '05:23:44',
           'sunriseEpoch': 1620944624,
           'sunset': '18:23:41',
           'sunsetEpoch': 1620991421,
           'temp': 29.6,
           'tempmax': 32.7,
           'tempmin'

In [6]:
table = convert_to_table(data)
df = pd.DataFrame(table)

In [7]:
df.to_csv('NgheAn.csv', sep=',', encoding='utf-8', index=False, header=True)

#### Đợt thứ tư: Từ ngày 1/9/2021 đến 1/1/2024 ở Nghệ An.

In [8]:
data = fetch_weather_data(locations[1], '2021-09-01', '2024-01-01')
print_data(data)

2021-09-01 2024-01-01
dict_keys(['queryCost', 'latitude', 'longitude', 'resolvedAddress', 'address', 'timezone', 'tzoffset', 'days', 'stations'])
<class 'list'>
{'cloudcover': 59.4,
 'conditions': 'Rain, Partially cloudy',
 'datetime': '2021-09-01',
 'datetimeEpoch': 1630429200,
 'description': 'Partly cloudy throughout the day with a chance of rain '
                'throughout the day.',
 'dew': 25.6,
 'feelslike': 34.4,
 'feelslikemax': 39.3,
 'feelslikemin': 26.1,
 'humidity': 82.4,
 'icon': 'rain',
 'moonphase': 0.81,
 'precip': 4.2,
 'precipcover': 41.67,
 'precipprob': 100.0,
 'preciptype': ['rain'],
 'pressure': 1008.3,
 'snow': 0.0,
 'snowdepth': 0.0,
 'solarenergy': 22.2,
 'solarradiation': 255.7,
 'source': 'obs',
 'stations': ['48845099999', 'remote'],
 'sunrise': '05:42:27',
 'sunriseEpoch': 1630449747,
 'sunset': '18:11:53',
 'sunsetEpoch': 1630494713,
 'temp': 29.0,
 'tempmax': 31.6,
 'tempmin': 26.1,
 'uvindex': 9.0,
 'visibility': 20.0,
 'winddir': 43.9,
 'windgust': 2

In [9]:
# In ra dữ liệu theo định dạng JSON đã thu thập được từ API
pprint(data)

{'address': 'Nghe An',
 'days': [{'cloudcover': 59.4,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2021-09-01',
           'datetimeEpoch': 1630429200,
           'description': 'Partly cloudy throughout the day with a chance of '
                          'rain throughout the day.',
           'dew': 25.6,
           'feelslike': 34.4,
           'feelslikemax': 39.3,
           'feelslikemin': 26.1,
           'humidity': 82.4,
           'icon': 'rain',
           'moonphase': 0.81,
           'precip': 4.2,
           'precipcover': 41.67,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1008.3,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 22.2,
           'solarradiation': 255.7,
           'source': 'obs',
           'stations': ['48845099999', 'remote'],
           'sunrise': '05:42:27',
           'sunriseEpoch': 1630449747,
           'sunset': '18:11:53',
           'sunse

           'feelslike': 21.9,
           'feelslikemax': 26.1,
           'feelslikemin': 19.2,
           'humidity': 76.5,
           'icon': 'rain',
           'moonphase': 0.11,
           'precip': 6.1,
           'precipcover': 8.33,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1017.7,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 6.2,
           'solarradiation': 72.0,
           'source': 'obs',
           'stations': ['48845099999', 'remote'],
           'sunrise': '06:00:19',
           'sunriseEpoch': 1636326019,
           'sunset': '17:21:23',
           'sunsetEpoch': 1636366883,
           'temp': 21.9,
           'tempmax': 26.1,
           'tempmin': 19.2,
           'uvindex': 3.0,
           'visibility': 15.5,
           'winddir': 2.3,
           'windgust': 62.3,
           'windspeed': 33.1},
          {'cloudcover': 78.2,
           'conditions': 'Partially cloudy',
           'datetim

           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1003.4,
           'severerisk': 60.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 15.3,
           'solarradiation': 178.8,
           'source': 'obs',
           'stations': ['48845099999', 'remote', '48846099999'],
           'sunrise': '05:25:37',
           'sunriseEpoch': 1657059937,
           'sunset': '18:38:18',
           'sunsetEpoch': 1657107498,
           'temp': 29.6,
           'tempmax': 36.4,
           'tempmin': 26.7,
           'uvindex': 8.0,
           'visibility': 22.0,
           'winddir': 283.1,
           'windgust': 21.6,
           'windspeed': 12.6},
          {'cloudcover': 95.0,
           'conditions': 'Rain, Overcast',
           'datetime': '2022-07-07',
           'datetimeEpoch': 1657126800,
           'description': 'Cloudy skies throughout the day with rain.',
           'dew': 24.2,
           'feelslike': 33.4,
        

           'tempmin': 15.7,
           'uvindex': 7.0,
           'visibility': 22.7,
           'winddir': 346.7,
           'windgust': 14.0,
           'windspeed': 11.9},
          {'cloudcover': 86.7,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2022-12-27',
           'datetimeEpoch': 1672074000,
           'description': 'Partly cloudy throughout the day with a chance of '
                          'rain throughout the day.',
           'dew': 17.3,
           'feelslike': 20.2,
           'feelslikemax': 22.1,
           'feelslikemin': 19.0,
           'humidity': 83.5,
           'icon': 'rain',
           'moonphase': 0.13,
           'precip': 1.6,
           'precipcover': 37.5,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1018.8,
           'severerisk': 10.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 11.0,
           'solarradiation': 129.9,
           'source'

          {'cloudcover': 43.9,
           'conditions': 'Partially cloudy',
           'datetime': '2023-04-20',
           'datetimeEpoch': 1681923600,
           'description': 'Partly cloudy throughout the day.',
           'dew': 24.1,
           'feelslike': 29.3,
           'feelslikemax': 36.9,
           'feelslikemin': 24.9,
           'humidity': 84.2,
           'icon': 'partly-cloudy-day',
           'moonphase': 0.0,
           'precip': 0.0,
           'precipcover': 0.0,
           'precipprob': 0.0,
           'preciptype': None,
           'pressure': 1000.2,
           'severerisk': 30.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 22.8,
           'solarradiation': 265.1,
           'source': 'obs',
           'stations': ['48845099999', 'remote', '48846099999'],
           'sunrise': '05:37:10',
           'sunriseEpoch': 1681943830,
           'sunset': '18:15:41',
           'sunsetEpoch': 1681989341,
           'temp': 27.1,
   

           'winddir': 73.0,
           'windgust': 15.5,
           'windspeed': 16.6},
          {'cloudcover': 67.2,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2023-05-10',
           'datetimeEpoch': 1683651600,
           'description': 'Partly cloudy throughout the day with rain.',
           'dew': 24.9,
           'feelslike': 30.7,
           'feelslikemax': 39.8,
           'feelslikemin': 25.2,
           'humidity': 86.4,
           'icon': 'rain',
           'moonphase': 0.66,
           'precip': 0.8,
           'precipcover': 16.67,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1008.7,
           'severerisk': 30.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 24.4,
           'solarradiation': 284.1,
           'source': 'obs',
           'stations': ['48845099999', 'remote', '48846099999'],
           'sunrise': '05:25:34',
           'sunriseEpoch': 1683671134,

           'windspeed': 18.0},
          {'cloudcover': 99.5,
           'conditions': 'Rain, Overcast',
           'datetime': '2023-06-24',
           'datetimeEpoch': 1687539600,
           'description': 'Cloudy skies throughout the day with late afternoon '
                          'rain.',
           'dew': 25.1,
           'feelslike': 34.1,
           'feelslikemax': 40.5,
           'feelslikemin': 29.8,
           'humidity': 80.8,
           'icon': 'rain',
           'moonphase': 0.2,
           'precip': 0.1,
           'precipcover': 4.17,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1003.6,
           'severerisk': 60.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 4.2,
           'solarradiation': 48.8,
           'source': 'obs',
           'stations': ['48845099999', 'remote', '48846099999'],
           'sunrise': '05:22:05',
           'sunriseEpoch': 1687558925,
           'sunset': '18:

          {'cloudcover': 97.7,
           'conditions': 'Rain, Overcast',
           'datetime': '2023-08-05',
           'datetimeEpoch': 1691168400,
           'description': 'Cloudy skies throughout the day with late afternoon '
                          'rain.',
           'dew': 22.7,
           'feelslike': 32.2,
           'feelslikemax': 35.2,
           'feelslikemin': 29.1,
           'humidity': 69.7,
           'icon': 'rain',
           'moonphase': 0.62,
           'precip': 0.2,
           'precipcover': 4.17,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1002.9,
           'severerisk': 10.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 7.1,
           'solarradiation': 84.3,
           'source': 'obs',
           'stations': ['48845099999', 'remote', '48846099999'],
           'sunrise': '05:35:46',
           'sunriseEpoch': 1691188546,
           'sunset': '18:30:43',
           'sunsetEpoc

           'moonphase': 0.42,
           'precip': 57.0,
           'precipcover': 12.5,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1006.8,
           'severerisk': 30.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 12.9,
           'solarradiation': 147.5,
           'source': 'obs',
           'stations': ['48845099999', 'remote', '48846099999'],
           'sunrise': '05:46:53',
           'sunriseEpoch': 1695768413,
           'sunset': '17:49:48',
           'sunsetEpoch': 1695811788,
           'temp': 26.7,
           'tempmax': 28.9,
           'tempmin': 25.4,
           'uvindex': 6.0,
           'visibility': 10.0,
           'winddir': 79.2,
           'windgust': 31.3,
           'windspeed': 22.7},
          {'cloudcover': 93.6,
           'conditions': 'Rain, Overcast',
           'datetime': '2023-09-28',
           'datetimeEpoch': 1695834000,
           'description': 'Cloudy skies throug

           'windspeed': 14.4},
          {'cloudcover': 77.5,
           'conditions': 'Rain, Partially cloudy',
           'datetime': '2023-11-24',
           'datetimeEpoch': 1700758800,
           'description': 'Partly cloudy throughout the day with late '
                          'afternoon rain.',
           'dew': 20.4,
           'feelslike': 23.4,
           'feelslikemax': 25.2,
           'feelslikemin': 21.9,
           'humidity': 83.5,
           'icon': 'rain',
           'moonphase': 0.39,
           'precip': 1.5,
           'precipcover': 4.17,
           'precipprob': 100.0,
           'preciptype': ['rain'],
           'pressure': 1017.0,
           'severerisk': 10.0,
           'snow': 0.0,
           'snowdepth': 0.0,
           'solarenergy': 11.1,
           'solarradiation': 129.2,
           'source': 'obs',
           'stations': ['48845099999', 'remote', '48846099999'],
           'sunrise': '06:08:56',
           'sunriseEpoch': 1700780936,
           's

In [10]:
table = convert_to_table(data)
df_new = pd.DataFrame(table)

In [11]:
df_old = pd.read_csv('NgheAn.csv')
df_old.head(5)

Datetime  Tempmax  Tempmin  Temp   Dew  Feelslike  Precip  Precipprob  \
0  2019-01-01     15.0     12.9  14.0  10.3       14.0     0.0         0.0   
1  2019-01-02     15.8     12.2  14.3  10.8       14.3     0.9       100.0   
2  2019-01-03     17.7     14.5  16.1  13.1       16.1     0.4       100.0   
3  2019-01-04     20.1     16.2  17.9  15.2       17.9     0.1       100.0   
4  2019-01-05     21.7     17.9  19.5  17.1       19.5     0.0         0.0   

   Precipcover Preciptype  ...  Solarenergy  Uvindex   Sunrise    Sunset  \
0         0.00        NaN  ...          4.6      2.0  06:29:44  17:31:24   
1         4.17   ['rain']  ...          3.3      2.0  06:30:04  17:32:01   
2        16.67   ['rain']  ...          5.5      3.0  06:30:23  17:32:37   
3         4.17   ['rain']  ...          4.3      2.0  06:30:42  17:33:14   
4         0.00        NaN  ...          3.9      2.0  06:30:59  17:33:52   

   Moonphase    Icon      Conditions  \
0       0.83  cloudy        Overcast   
1       0.87    rain  Rain, Overcast   
2       0.90    rain  Rain, Overcast   
3       0.94    rain  Rain, Overcast   
4       0.97  cloudy        Overcast   

                                         Description  \
0                   Cloudy skies throughout the day.   
1  Cloudy skies throughout the day with morning r...   
2  Cloudy skies throughout the day with early mor...   
3  Cloudy skies throughout the day with early mor...   
4                   Cloudy skies throughout the day.   

                                   Stations  Address  
0  ['48845099999', 'remote', '48846099999']  Nghe An  
1  ['48845099999', 'remote', '48846099999']  Nghe An  
2                 ['48845099999', 'remote']  Nghe An  
3                 ['48845099999', 'remote']  Nghe An  
4                 ['48845099999', 'remote']  Nghe An  

[5 rows x 30 columns]

In [12]:
df_combined = pd.concat([df_old, df_new], ignore_index=True)
df_combined.to_csv('NgheAn.csv', sep=',', encoding='utf-8', index=False, header=True)